In [ ]:
!pip install transformers
!pip install plotly==4.14.1
!pip install datasets

In [ ]:
!pip install datasets

In [ ]:
import torch
import pandas as pd
import plotly.express as px
from transformers import BertTokenizer, BertModel
from datasets import load_dataset
from torch.utils.data import DataLoader

from collections import defaultdict
from sklearn.metrics.pairwise import euclidean_distances, cosine_distances
from scipy.spatial.distance import euclidean, pdist, squareform
from sklearn import manifold          #use this for MDS computation

#visualization libs
import plotly.graph_objects as go
import matplotlib.pyplot as plt
% matplotlib inline

In [ ]:
pd.set_option('max_colwidth', 800)

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print('using device: ', torch.cuda.get_device_name(device), flush=True)

using device:  Tesla T4


In [ ]:
# Load pre-trained model tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

In [ ]:
# Load pre-trained model
model = BertModel.from_pretrained('bert-base-uncased',
                                  output_hidden_states = True
                                  )
model.to(device)
# Put the model in "evaluation" mode
model.eval()

In [26]:
#from google.colab import files
uploaded = files.upload()
#df = pd.read_csv('stupidstuff.csv', encoding='utf-8')

Saving stopwords-en.txt to stopwords-en.txt


In [18]:
import io
df = pd.read_csv(io.BytesIO(uploaded['stupidstuff.csv']))

In [19]:
df.head(5)

body  ... rating
0                                                                                                                                                                                                                              A blackjack dealer and a player with a thirteen count in his hand\r\nwere arguing about whether or not it was appropriate to tip the\r\ndealer.\r\n\r\nThe player said, "When I get bad cards, it's not the dealer's fault.\r\nAccordingly, when I get good cards, the dealer obviously had nothing\r\nto do with it so, why should I tip him?"\r\n\r\nThe dealer said, "When you eat out do you tip the waiter?"\r\n\r\n"Yes."\r\n\r\n"Well then, he serves you food, I'm serving you cards, so you should\r\ntip me."\r\n\r\n"Okay, but, the waiter gives me what I ask for. I'll take an eight."  ...   2.63
1                                                                                                                                                                                                                                                                                                                                                                   At a dinner party, several of the guests were arguing whether men or women were more trustworthy. 'No woman,' said one man, scornfully, 'can keep a secret.' 'I don't know about that,' answered a blonde woman guest. 'I have kept my age a secret since I was twenty-one.' 'You'll let it out some day,' the man insisted. 'I hardly think so!' responded the blonde lady. 'When a woman has kept a secret for twenty-seven years, she can keep it forever.'  ...   2.57
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 One day this cop pulls over a blonde for speeding. The cop gets out of his car and asks the blonde for her license.''You cops should get it together. One day you take away my license and the next day you ask me to show it.''  ...   3.09
3  Three women are about to be executed for crimes. One's a brunette, one's a redhead, and one's a blonde.Two guards brings the brunette forward, and the executioner asks if she has any last requests. She says no, and the executioner shouts, "Ready . . . Aim . . ."Suddenly the brunette yells, "earthquake!!" Everyone is startled and looks around. She manages to escape.The angry guards then bring the redhead forward, and the executioner asks if she has any last requests. She says no, and the executioner shouts, "Ready . . . Aim . . ."The redhead then screams, "tornado!!" Yet again, everyone is startled and looks around. She too escapes execution.By this point, the blonde had figured out what the others did. The guards bring her forward, and the executioner asks if she has any last requests....  ...   4.10
4  A girl came skipping home FROM school one day. "Mommy, Mommy," she yelled, "we were counting today, and all the other kids could only count to four, but I counted to 10. See? 1, 2, 3, 4, 5, 6,7, 8, 9, 10!" "Very good," said her mother. "Is it because I'm blonde, Mommy?" "Yes, Honey, it's because you're blonde." The next day the girl came skipping home FROM school. "Mommy, Mommy," She yelled, "we were saying the alphabet today, and all the other kids could only say it to D, but I said it to G. See? A,b, c, d, e, f, g!" "Very good," said her mother. "Is it because I'm blonde, Mommy?" "Yes, Honey, it's because you're blonde." The next day the girl came skipping home FROM school. "Mommy, Mommy," she yelled, "we wer

In [20]:
df.sample(5)

body  ... rating
1091                                                                                                                                                                                                                                                                                                                                                                                                                                            What bird represents freedom ?The EagleWhat bird represents peace ?The DoveWhat bird represents true love ?The Swallow  ...    2.0
2186                                                                                                                                                                                                                                                                         The phone rings in the maternity ward. Upon answering, the duty midwife is told by a man "Mrs Jones is about to give birth, her contractions are just 3 minutes apart!"\r\nThe midwife asks "Is this her first Child?"\r\nBemused, the man says "No, don't be daft, this is her Husband!"  ...    4.0
1777                                                                                                                                                                                                                                                                           Today's woman puts on wigs, fake eyelashes, false fingernails, sixteen pounds of assorted make-up/shadows/blushes/creams, living bras, various pads that would make a line-backer envious, has implants and assorted other surgeries, then complains that she cannot find a "real" man.  ...    2.0
2672  At 3 am a desk clerk at a hotel gets a call from a drunk guy asking what time the bar opens. "It opens at noon," answers the clerk. About an hour, later he gets a call from the same guy, sounding even drunker. "What time does the bar open?" he asks. "Same time as before - noon," replies the clerk. Another hour passes and he calls again, plastered. "Whatjoo shay the bar opins at?"The clerk then answers, "It opens at noon, but if you can't wait, I can have room service send something up to you." "No! I don't wanna git in, ah wanna git OUT!"  ...    2.0
1245                                                                          The devil visited a lawyer's office and made him an offer. "I can arrange some things for you, " the devil said. "I'll increase your income five-fold. Your partners will love you; your clients will respect you; you'll have four months of vacation each year and live to be a hundred. All I require in return is that your wife's soul, your children's souls, and their children's souls rot in hell for eternity."The lawyer thought for a moment and asked, "What's the catch?".  ...    3.0

[5 rows x 4 columns]

In [21]:
inputs = tokenizer("Why do bald men cut holes in their pockets? So they can run their fingerz through their hair.")

In [22]:
inputs

{'input_ids': [101, 2339, 2079, 13852, 2273, 3013, 8198, 1999, 2037, 10306, 1029, 2061, 2027, 2064, 2448, 2037, 4344, 2480, 2083, 2037, 2606, 1012, 102], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

In [23]:
len(inputs['input_ids'])

23

In [24]:
tokenizer.convert_ids_to_tokens(inputs['input_ids'])

['[CLS]',
 'why',
 'do',
 'bald',
 'men',
 'cut',
 'holes',
 'in',
 'their',
 'pockets',
 '?',
 'so',
 'they',
 'can',
 'run',
 'their',
 'finger',
 '##z',
 'through',
 'their',
 'hair',
 '.',
 '[SEP]']

In [27]:
stopwords = []
with open('stopwords-en.txt', encoding='utf-8') as f:
  for line in f:
    stopwords.append(line.strip())

In [28]:
stopwords[:10]

["'ll", "'tis", "'twas", "'ve", '10', '39', 'a', "a's", 'able', 'ableabout']

In [29]:
subsample = df.iloc[:1000].copy()

In [30]:
from collections import Counter

In [31]:
def get_repetitions(text):
    token_list = text.split()
    counts = Counter()

    for token in token_list:
      if token in stopwords:
        continue
      counts[token] += 1

    # return word with most repetitions, if exists
    top_word, top_count = counts.most_common(1)[0]
    if top_count > 1:
      return top_word
    return None

In [76]:
%%time
subsample.loc[:, 'repeated'] = subsample['body'].str.lower().apply(get_repetitions)

CPU times: user 1.57 s, sys: 589 µs, total: 1.57 s
Wall time: 1.57 s


In [33]:
subsample.head(5)

body  ... rating
0                                                                                                                                                                                                                              A blackjack dealer and a player with a thirteen count in his hand\r\nwere arguing about whether or not it was appropriate to tip the\r\ndealer.\r\n\r\nThe player said, "When I get bad cards, it's not the dealer's fault.\r\nAccordingly, when I get good cards, the dealer obviously had nothing\r\nto do with it so, why should I tip him?"\r\n\r\nThe dealer said, "When you eat out do you tip the waiter?"\r\n\r\n"Yes."\r\n\r\n"Well then, he serves you food, I'm serving you cards, so you should\r\ntip me."\r\n\r\n"Okay, but, the waiter gives me what I ask for. I'll take an eight."  ...   2.63
1                                                                                                                                                                                                                                                                                                                                                                   At a dinner party, several of the guests were arguing whether men or women were more trustworthy. 'No woman,' said one man, scornfully, 'can keep a secret.' 'I don't know about that,' answered a blonde woman guest. 'I have kept my age a secret since I was twenty-one.' 'You'll let it out some day,' the man insisted. 'I hardly think so!' responded the blonde lady. 'When a woman has kept a secret for twenty-seven years, she can keep it forever.'  ...   2.57
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 One day this cop pulls over a blonde for speeding. The cop gets out of his car and asks the blonde for her license.''You cops should get it together. One day you take away my license and the next day you ask me to show it.''  ...   3.09
3  Three women are about to be executed for crimes. One's a brunette, one's a redhead, and one's a blonde.Two guards brings the brunette forward, and the executioner asks if she has any last requests. She says no, and the executioner shouts, "Ready . . . Aim . . ."Suddenly the brunette yells, "earthquake!!" Everyone is startled and looks around. She manages to escape.The angry guards then bring the redhead forward, and the executioner asks if she has any last requests. She says no, and the executioner shouts, "Ready . . . Aim . . ."The redhead then screams, "tornado!!" Yet again, everyone is startled and looks around. She too escapes execution.By this point, the blonde had figured out what the others did. The guards bring her forward, and the executioner asks if she has any last requests....  ...   4.10
4  A girl came skipping home FROM school one day. "Mommy, Mommy," she yelled, "we were counting today, and all the other kids could only count to four, but I counted to 10. See? 1, 2, 3, 4, 5, 6,7, 8, 9, 10!" "Very good," said her mother. "Is it because I'm blonde, Mommy?" "Yes, Honey, it's because you're blonde." The next day the girl came skipping home FROM school. "Mommy, Mommy," She yelled, "we were saying the alphabet today, and all the other kids could only say it to D, but I said it to G. See? A,b, c, d, e, f, g!" "Very good," said her mother. "Is it because I'm blonde, Mommy?" "Yes, Honey, it's because you're blonde." The next day the girl came skipping home FROM school. "Mommy, Mommy," she yelled, "we wer

In [40]:
na_rows = df[df['body'].isna()]

In [41]:
df = df.drop(na_rows.index)

In [42]:
df.shape

(3200, 4)

In [43]:
%%time
# tokenize without padding and truncation first
encodings = tokenizer(df['body'].to_list())

Token indices sequence length is longer than the specified maximum sequence length for this model (514 > 512). Running this sequence through the model will result in indexing errors


CPU times: user 7.22 s, sys: 7.26 ms, total: 7.22 s
Wall time: 7.24 s


In [44]:
lens = [len(ex) for ex in encodings['input_ids']]

In [45]:
lens_series = pd.Series(lens, name='number_of_tokens')

In [46]:
lens_series

0       142
1       122
2        57
3       219
4       301
       ... 
3195    249
3196     23
3197    289
3198    702
3199     66
Name: number_of_tokens, Length: 3200, dtype: int64

In [47]:
lens_series.describe()

count    3200.000000
mean      171.060625
std       163.989821
min         3.000000
25%        54.000000
50%       140.500000
75%       232.000000
max      2371.000000
Name: number_of_tokens, dtype: float64

In [48]:
fig = px.histogram(lens_series, x="number_of_tokens", range_x=[0, 1000])
fig.show()

In [49]:
lens_series[lens_series > 512].shape

(95,)

In [50]:
# take only jokes that have <= 300 tokens
short_indices = [i for i, length in lens_series.iteritems() if length <= 300]
df_short = df.iloc[short_indices].copy()

In [51]:
df_short.shape

(2759, 4)

In [52]:
# take a subsample of this for testing
df_sub = df_short.iloc[:1000].copy()

In [53]:
# source: https://colab.research.google.com/github/nidharap/Notebooks/blob/master/Word_Embeddings_BERT.ipynb#scrollTo=2OGCu6P6exFS
# Create a function to tokenize a set of texts
def preprocessing_for_bert(data, tokenizer_obj):
    """Perform required preprocessing steps for pretrained BERT.
    @param    data (np.array): Array of texts to be processed.
    @return   input_ids (torch.Tensor): Tensor of token ids to be fed to a model.
    @return   attention_masks (torch.Tensor): Tensor of indices specifying which
                  tokens should be attended to by the model.
    @return   attention_masks_without_special_tok (torch.Tensor): Tensor of indices specifying which
                  tokens should be attended to by the model excluding the special tokens (CLS/SEP)
    """
    # Create empty lists to store outputs
    input_ids = []
    attention_masks = []

    # For every sentence...
    for sent in data:
        # `encode` will:
        #    (1) Tokenize the sentence
        #    (2) Add the `[CLS]` and `[SEP]` token to the start and end
        #    (3) Truncate/Pad sentence to max length
        #    (4) Map tokens to their IDs
        #    (5) Create attention mask
        #    (6) Return a dictionary of outputs
        encoded_sent = tokenizer(
            text=sent,  # Preprocess sentence
            padding='max_length',         # Pad sentence to max length
            truncation=True,              # Shouldn't be necessary for us
            )
        
        # Add the outputs to the lists
        input_ids.append(encoded_sent.get('input_ids'))
        attention_masks.append(encoded_sent.get('attention_mask'))

    # Convert lists to tensors
    input_ids = torch.tensor(input_ids)
    attention_masks = torch.tensor(attention_masks)
    
    #lets create another mask that will be useful when we want to average all word vectors later
    #we would like to average across all word vectors in a sentence, but excluding the CLS and SEP token
    #create a copy
    attention_masks_without_special_tok = attention_masks.clone().detach()
    
    #set the CLS token index to 0 for all sentences 
    attention_masks_without_special_tok[:,0] = 0

    #get sentence lengths and use that to set those indices to 0 for each length
    #essentially, the last index for each sentence, which is the SEP token
    sent_len = attention_masks_without_special_tok.sum(1).tolist()

    #column indices to set to zero
    col_idx = torch.LongTensor(sent_len)
    #row indices for all rows
    row_idx = torch.arange(attention_masks.size(0)).long()
    
    #set the SEP indices for each sentence token to zero
    attention_masks_without_special_tok[row_idx, col_idx] = 0

    return input_ids, attention_masks, attention_masks_without_special_tok

In [54]:
%%time
#run sentences through the tokenizer
#input_ids, attention_masks, attention_masks_without_special_tok = preprocessing_for_bert(df_sub['text'].to_list(), tokenizer)

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 5.96 µs


In [56]:
%%time
encodings = tokenizer(
            df_sub['body'].to_list(),
            padding='max_length',         # Pad sentence to max length
            truncation=True,              # Shouldn't be necessary for us
            #return_tensors="pt"
            )

CPU times: user 2.13 s, sys: 4.48 ms, total: 2.13 s
Wall time: 2.14 s


In [57]:
encodings.items()

dict_items([('input_ids', [[101, 1037, 2304, 17364, 11033, 1998, 1037, 2447, 2007, 1037, 7093, 4175, 1999, 2010, 2192, 2020, 9177, 2055, 3251, 2030, 2025, 2009, 2001, 6413, 2000, 5955, 1996, 11033, 1012, 1996, 2447, 2056, 1010, 1000, 2043, 1045, 2131, 2919, 5329, 1010, 2009, 1005, 1055, 2025, 1996, 11033, 1005, 1055, 6346, 1012, 11914, 1010, 2043, 1045, 2131, 2204, 5329, 1010, 1996, 11033, 5525, 2018, 2498, 2000, 2079, 2007, 2009, 2061, 1010, 2339, 2323, 1045, 5955, 2032, 1029, 1000, 1996, 11033, 2056, 1010, 1000, 2043, 2017, 4521, 2041, 2079, 2017, 5955, 1996, 15610, 1029, 1000, 1000, 2748, 1012, 1000, 1000, 2092, 2059, 1010, 2002, 4240, 2017, 2833, 1010, 1045, 1005, 1049, 3529, 2017, 5329, 1010, 2061, 2017, 2323, 5955, 2033, 1012, 1000, 1000, 3100, 1010, 2021, 1010, 1996, 15610, 3957, 2033, 2054, 1045, 3198, 2005, 1012, 1045, 1005, 2222, 2202, 2019, 2809, 1012, 1000, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [58]:
class Dataset(torch.utils.data.Dataset):
    def __init__(self, encodings):
        self.encodings = encodings

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        return item

    def __len__(self):
        return len(self.encodings['input_ids'])

In [59]:
dataset = Dataset(encodings)

In [60]:
# took small batch size for now to get less cluttered visualization
data_loader = DataLoader(dataset, batch_size=2)

In [61]:
# number of batches in our dataset
len(data_loader)

500

In [62]:
all_hidden_states = []
all_input_ids = []
all_attention_masks = []
# need to process batch by batch, otherwise will run out of RAM
for batch in data_loader:
    # Load batch to GPU
    input_ids = batch['input_ids'].to(device)
    attention_mask = batch['attention_mask'].to(device)
    print(input_ids)

    with torch.no_grad():
        outputs = model(input_ids, attention_mask=attention_mask)
        # outputs include:
        # 1) last_hidden_state (torch.FloatTensor of shape (batch_size, sequence_length, hidden_size)) – Sequence of hidden-states at the output of the last layer of the model.
        # 2) pooler_output (torch.FloatTensor of shape (batch_size, hidden_size)) – Last layer hidden-state of the first token of the sequence (classification token) further processed by a Linear layer and a Tanh activation function. The Linear layer weights are trained from the next sentence prediction (classification) objective during pretraining.
        # 3) hidden_states (tuple(torch.FloatTensor), optional, returned when output_hidden_states=True is passed or when config.output_hidden_states=True) – Tuple of torch.FloatTensor (one for the output of the embeddings + one for the output of each layer) of shape (batch_size, sequence_length, hidden_size).
        # Hidden-states of the model at the output of each layer plus the initial embedding outputs.
        # 4) attentions (tuple(torch.FloatTensor), optional, returned when output_attentions=True is passed or when config.output_attentions=True) – Tuple of torch.FloatTensor (one for each layer) of shape (batch_size, num_heads, sequence_length, sequence_length).
        # Attentions weights after the attention softmax, used to compute the weighted average in the self-attention heads.
        # 5) cross_attentions (tuple(torch.FloatTensor), optional, returned when output_attentions=True and config.add_cross_attention=True is passed or when config.output_attentions=True) – Tuple of torch.FloatTensor (one for each layer) of shape (batch_size, num_heads, sequence_length, sequence_length).
        # Attentions weights of the decoder’s cross-attention layer, after the attention softmax, used to compute the weighted average in the cross-attention heads.
        
        hidden_states = outputs[2]
        # this gives us a tuple of length 13 which includes a [batch_size, max_len, hidden_dim] hidden states for each layer 
        print("Total hidden layers:", len(hidden_states))
        print("First layer : hidden_states[0].shape ", hidden_states[0].shape)  # [batch_size, max_len, hidden_dim]
        # append current batch hidden states to all hidden states
        all_hidden_states.append(hidden_states)
        # store current batch details for visualization purposes
        all_input_ids.append(batch['input_ids'])
        all_attention_masks.append(batch['attention_mask'])
    
    break

tensor([[ 101, 1037, 2304,  ...,    0,    0,    0],
        [ 101, 2012, 1037,  ...,    0,    0,    0]], device='cuda:0')
Total hidden layers: 13
First layer : hidden_states[0].shape  torch.Size([2, 512, 768])


In [63]:
def get_vector(hidden_layers_form_arch, token_index=0, mode='average', top_n_layers=4):
  '''
  retrieve vectors for a token_index from the top n layers and return a concatenated, averaged or summed vector 
  hidden_layers_form_arch: tuple returned by the transformer library
  token_index: index of the token for which a vector is desired
  mode=
        'average' : avg last n layers
        'concat': concatenate last n layers
        'sum' : sum last n layers
        'last': return embeddings only from last layer
        'second_last': return embeddings only from second last layer

  top_n_layers: number of top layers to concatenate/ average / sum
  '''
  if mode == 'concat':
    #concatenate last 4 layer outputs -> returns [batch_size x seq_len x dim]
    #permute(1,0,2) swaps the the batch and seq_len dim , making it easy to return all the vectors for a particular token position
    return torch.cat(hidden_layers_form_arch[-top_n_layers:], dim=2).permute(1,0,2)[token_index]
  
  if mode == 'average':
    #avg last 4 layer outputs -> returns [batch_size x seq_len x dim]
    return torch.stack(hidden_layers_form_arch[-top_n_layers:]).mean(0).permute(1,0,2)[token_index]


  if mode == 'sum':
    #sum last 4 layer outputs -> returns [batch_size x seq_len x dim]
    return torch.stack(hidden_layers_form_arch[-top_n_layers:]).sum(0).permute(1,0,2)[token_index]


  if mode == 'last':
    #last layer output -> returns [batch_size x seq_len x dim]
    return hidden_layers_form_arch[-1:][0].permute(1,0,2)[token_index]

  if mode == 'second_last':
    #last layer output -> returns [batch_size x seq_len x dim]
    return hidden_layers_form_arch[-2:-1][0].permute(1,0,2)[token_index]

  return None

In [64]:
# this gives us the output of the last layer for tokens at position 1 in all sentences of the first batch
get_vector(all_hidden_states[0], token_index=1, mode='last').shape

torch.Size([2, 768])

In [65]:
# get information about the batch we are going to visualize
input_ids = all_input_ids[0]
attention_mask = all_attention_masks[0]

In [71]:
#Lengths of each sentence
sent_lengths = attention_mask.sum(1).tolist()
sent_lengths

[142, 122]

In [ ]:
#get the tokenized version of each sentence (text form, to label things in the plot)
tokenized_sents = [tokenizer.convert_ids_to_tokens(i) for i in input_ids]
tokenized_sents[0][:50]

In [73]:
def plt_dists(dists, labels, dims=2, words_of_interest=[], title=""):
  '''
  Plot distances using MDS in 2D/3D 
  dists: precomputed distance matrix
  labels: labels to display on the plot
  dims: 2/3 for 2 or 3 dimensional plot, defaults to 2 for any other value passed
  words_of_interest: list of words to highlight with a different color
  title: title for the plot
  '''
  cnt_dict = dict()
  color = list()

  #separate colors for words that are in words_of_interest vs other
  #each word will have a _SentenceNumber at the end to differentiate the words coming in from different sentences
  for v in labels:
    found = False
    for wrd_int in words_of_interest:
      if wrd_int in v:
        found = True
        break
      
    if found:
      color.append(1)
    else:
      color.append(0)

  #https://community.plotly.com/t/plotly-colours-list/11730/6
  colorscale = [[0, 'darkcyan'], [1, 'white']]

  #dists is precomputed using cosine similarity and passed
  #calculate MDS with number of dims passed
  mds = manifold.MDS(n_components=dims, dissimilarity="precomputed", random_state=60, max_iter=90000)
  results = mds.fit(dists)

  #get coodinates for each point
  coords = results.embedding_

  #plot
  if dims == 3:
    fig = go.Figure(data=[go.Scatter3d(
        x=coords[:, 0],
        y=coords[:, 1],
        z=coords[:, 2],
        mode='markers+text',
        textposition="top center",
        text=labels,
        marker=dict(
            size=10,
            color=color,
            colorscale=colorscale,
            opacity=0.8,
            
        )
    )])
  else:
    fig = go.Figure(data=[go.Scatter(
        x=coords[:, 0],
        y=coords[:, 1],
        mode='markers+text',
        text=labels,
        textposition="top center",
        marker=dict(
            size=12,
            color=color,
            colorscale=colorscale,
            opacity=0.8,
            
        )
    )])

  fig.update_layout(template="plotly_dark")
  if title!="":
    fig.update_layout(title_text=title)
  fig.show()

In [74]:
def eval_vecs(input_hidden_states, input_tokenized_sents, mode='concat', top_n_layers=4, viz_dims=2, words_with_diff_color=[], max_len=512):
  '''
  function to get a vectors for each word in each sentence, add the sentence number to the end of each word
  calculate cosine distance between each pair of words and then pass it to the visualization function

  inputs:
  input_hidden_states: hiddent states retrieved from a BERT-like model
  input_tokenized_sents: tokenized sentences, used to assign labels for each point on the plot
  model:  'average' : avg last n layers
          'concat': concatenate last n layers
          'sum' : sum last n layers
          'last':  embeddings only from last layer
          'second_last':  embeddings only from second last layer
  top_n_layers: top n layers to use for concat/sum etc.
  viz_dims: 2/3 for 2D or 3D plot
  words_with_diff_color: words that should be highlighed with different color on the plot
  '''
  vecs = list()
  labels = list()
  for token_ind in range(max_len):
    if token_ind == 0:
      #ignore CLS
      continue
    vectors = get_vector(input_hidden_states, token_index=token_ind, mode=mode, top_n_layers=top_n_layers)
    for sent_ind, sent_len in enumerate(sent_lengths):
      if token_ind < sent_len-1:
        #ignore SEP which will be at the last index of each sentence
        vecs.append(vectors[sent_ind].cpu())
        labels.append(input_tokenized_sents[sent_ind][token_ind]+"_"+str(sent_ind))
    
  #create a numpy matrix to pass to cosine distance
  mat = torch.stack(vecs).detach().numpy()
  #call the plot function on the cosine distance matrix
  plt_dists(cosine_distances(mat), labels=labels, dims=viz_dims, words_of_interest=words_with_diff_color, title='Method: {}'.format(mode))

In [75]:
eval_vecs(all_hidden_states[0], tokenized_sents, mode='last', viz_dims=3, words_with_diff_color=['paint'], max_len=300)